In [5]:
from google.cloud import bigquery

In [6]:
client = bigquery.Client()

In [57]:
query = client.query("""
SELECT sentence FROM nlp.sentence
""")

In [58]:
from torch import Tensor, LongTensor
from torch.utils.data import Dataset, DataLoader
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.utils import to_categorical

In [59]:
class Sentences(Dataset):
    def __init__(self, sentences):
        self.sentences = sentences
        self.tokenizer = Tokenizer()
        self.tokenizer.fit_on_texts(sentences)
        self.seqs = self.tokenizer.texts_to_sequences(sentences)
        self.seq_input = pad_sequences(self.seqs)
        self.seq_output = pad_sequences(self.seqs, padding='post')
    
    def __getitem__(self, index):
        return LongTensor(self.seq_input[index]), LongTensor(self.seq_output[index])
    
    def __len__(self):
        return len(self.sentences)


In [60]:
sentences = Sentences([row['sentence']['sentence'] for row in query.result()])
data = DataLoader(sentences, batch_size=32, shuffle=True)

In [61]:
import torch
from torch.nn import CrossEntropyLoss
from torch.optim import Adam
from ml.sentence_generator.model import make_lstm

In [62]:
model = make_lstm(
    n_dim=20,
    n_layers=3,
    n_gaussian=3,
    n_words=len(sentences.tokenizer.index_word)
)
optimizer = Adam(model.parameters())
loss_func = CrossEntropyLoss()

In [ ]:
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
model.to(device)

In [63]:
def kl_loss(mu, sigma):
    return (torch.exp(sigma) + mu**2 - sigma - 1).mean()

In [64]:
def loss_func(tensor, label):
    length = label.shape[0] * label.shape[1]
    n_class = tensor.shape[-1]
    return CrossEntropyLoss()(tensor.view(length, n_class), label.view(length))

In [68]:
# train
for _ in range(1):
    for src, tgt in data:
        output, (mu, sigma) = model(src)
        output *= (src.flip(-1) > 0).view(*src.shape, 1) 
        loss = loss_func(output, tgt) + kl_loss(mu, sigma)
        loss.backward()
        optimizer.step()
        print(loss)

0 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
1 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
2 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
3 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
4 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
5 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
6 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
7 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
8 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
9 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
10 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
11 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
12 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
13 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
14 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
15 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
16 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
17 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
18 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
19 torch.Size([32, 1, 20]) torch.Size([3,

347 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
348 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
349 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
350 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
351 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
352 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
353 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
354 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
355 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
356 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
357 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
358 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
359 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
360 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
361 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
362 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
363 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
364 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
365 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
366 torch.Si

142 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
143 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
144 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
145 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
146 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
147 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
148 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
149 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
150 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
151 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
152 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
153 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
154 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
155 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
156 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
157 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
158 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
159 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
160 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
161 torch.Si

tensor(9.2096, grad_fn=<AddBackward0>)
0 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
1 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
2 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
3 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
4 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
5 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
6 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
7 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
8 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
9 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
10 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
11 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
12 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
13 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
14 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
15 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
16 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
17 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
18 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
19

163 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
164 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
165 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
166 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
167 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
168 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
169 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
170 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
171 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
172 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
173 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
174 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
175 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
176 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
177 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
178 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
179 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
180 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
181 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
182 torch.Si

...

tensor(9.0629, grad_fn=<AddBackward0>)
0 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
1 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
2 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
3 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
4 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
5 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
6 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
7 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
8 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
9 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
10 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
11 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
12 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
13 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
14 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
15 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
16 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
17 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
18 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
19

tensor(9.0711, grad_fn=<AddBackward0>)
0 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
1 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
2 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
3 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
4 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
5 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
6 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
7 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
8 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
9 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
10 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
11 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
12 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
13 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
14 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
15 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
16 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
17 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
18 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
19

tensor(9.0411, grad_fn=<AddBackward0>)
0 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
1 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
2 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
3 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
4 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
5 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
6 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
7 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
8 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
9 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
10 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
11 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
12 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
13 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
14 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
15 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
16 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
17 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
18 torch.Size([32, 1, 20]) torch.Size([3, 32, 20])
19

tensor(9.0558, grad_fn=<AddBackward0>)
0 torch.Size([26, 1, 20]) torch.Size([3, 26, 20])
1 torch.Size([26, 1, 20]) torch.Size([3, 26, 20])
2 torch.Size([26, 1, 20]) torch.Size([3, 26, 20])
3 torch.Size([26, 1, 20]) torch.Size([3, 26, 20])
4 torch.Size([26, 1, 20]) torch.Size([3, 26, 20])
5 torch.Size([26, 1, 20]) torch.Size([3, 26, 20])
6 torch.Size([26, 1, 20]) torch.Size([3, 26, 20])
7 torch.Size([26, 1, 20]) torch.Size([3, 26, 20])
8 torch.Size([26, 1, 20]) torch.Size([3, 26, 20])
9 torch.Size([26, 1, 20]) torch.Size([3, 26, 20])
10 torch.Size([26, 1, 20]) torch.Size([3, 26, 20])
11 torch.Size([26, 1, 20]) torch.Size([3, 26, 20])
12 torch.Size([26, 1, 20]) torch.Size([3, 26, 20])
13 torch.Size([26, 1, 20]) torch.Size([3, 26, 20])
14 torch.Size([26, 1, 20]) torch.Size([3, 26, 20])
15 torch.Size([26, 1, 20]) torch.Size([3, 26, 20])
16 torch.Size([26, 1, 20]) torch.Size([3, 26, 20])
17 torch.Size([26, 1, 20]) torch.Size([3, 26, 20])
18 torch.Size([26, 1, 20]) torch.Size([3, 26, 20])
19

tensor(9.0676, grad_fn=<AddBackward0>)
